In [48]:
import pandas as pd
import numpy as np
import csv
from pathlib import Path
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression

## Biodiversity Data

### Biodiversity - Working Data Attempt 1

In [2]:
#Load the species data from the species.csv file:

biodiversity_data_to_load = "./Resources/species.csv"
bio_df = pd.read_csv(biodiversity_data_to_load, low_memory=False)
bio_df.head()

Species ID             Park Name Category         Order    Family  \
0  ACAD-1000  Acadia National Park   Mammal  Artiodactyla  Cervidae   
1  ACAD-1001  Acadia National Park   Mammal  Artiodactyla  Cervidae   
2  ACAD-1002  Acadia National Park   Mammal     Carnivora   Canidae   
3  ACAD-1003  Acadia National Park   Mammal     Carnivora   Canidae   
4  ACAD-1004  Acadia National Park   Mammal     Carnivora   Canidae   

          Scientific Name                                       Common Names  \
0             Alces alces                                              Moose   
1  Odocoileus virginianus  Northern White-Tailed Deer, Virginia Deer, Whi...   
2           Canis latrans                             Coyote, Eastern Coyote   
3             Canis lupus        Eastern Timber Wolf, Gray Wolf, Timber Wolf   
4           Vulpes vulpes  Black Fox, Cross Fox, Eastern Red Fox, Fox, Re...   

  Record Status     Occurrence  Nativeness Abundance Seasonality  \
0      Approved        Present      Native      Rare    Resident   
1      Approved        Present      Native  Abundant         NaN   
2      Approved        Present  Not Native    Common         NaN   
3      Approved  Not Confirmed      Native       NaN         NaN   
4      Approved        Present     Unknown    Common     Breeder   

  Conservation Status Unnamed: 13  
0                 NaN         NaN  
1                 NaN         NaN  
2  Species of Concern         NaN  
3          Endangered         NaN  
4                 NaN         NaN

In [3]:
# Get the information for the species_df:
bio_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 119248 entries, 0 to 119247
Data columns (total 14 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   Species ID           119248 non-null  object
 1   Park Name            119248 non-null  object
 2   Category             119248 non-null  object
 3   Order                117776 non-null  object
 4   Family               117736 non-null  object
 5   Scientific Name      119248 non-null  object
 6   Common Names         119248 non-null  object
 7   Record Status        119248 non-null  object
 8   Occurrence           99106 non-null   object
 9   Nativeness           94203 non-null   object
 10  Abundance            76306 non-null   object
 11  Seasonality          20157 non-null   object
 12  Conservation Status  4718 non-null    object
 13  Unnamed: 13          5 non-null       object
dtypes: object(14)
memory usage: 12.7+ MB


In [4]:
# Creating new DataFrame with necessary data and leaving out unnecessary data
reduced_bio_df = bio_df[["Species ID", "Park Name", "Scientific Name",
                       "Occurrence", "Abundance", "Conservation Status"]].copy()
reduced_bio_df.head()

Species ID             Park Name         Scientific Name     Occurrence  \
0  ACAD-1000  Acadia National Park             Alces alces        Present   
1  ACAD-1001  Acadia National Park  Odocoileus virginianus        Present   
2  ACAD-1002  Acadia National Park           Canis latrans        Present   
3  ACAD-1003  Acadia National Park             Canis lupus  Not Confirmed   
4  ACAD-1004  Acadia National Park           Vulpes vulpes        Present   

  Abundance Conservation Status  
0      Rare                 NaN  
1  Abundant                 NaN  
2    Common  Species of Concern  
3       NaN          Endangered  
4    Common                 NaN

In [5]:
# Renaming Columns to standardize column names
renamed_bio_df = reduced_bio_df.rename(columns={"Species ID": "species_id",
                                        "Park Name": "park_name",
                                        "Scientific Name": "scientific_name",
                                        "Occurrence": "occurrence",
                                        "Abundance": "abundance",
                                        "Conservation Status": "conservation_status",
                                       })
renamed_bio_df.head()

species_id             park_name         scientific_name     occurrence  \
0  ACAD-1000  Acadia National Park             Alces alces        Present   
1  ACAD-1001  Acadia National Park  Odocoileus virginianus        Present   
2  ACAD-1002  Acadia National Park           Canis latrans        Present   
3  ACAD-1003  Acadia National Park             Canis lupus  Not Confirmed   
4  ACAD-1004  Acadia National Park           Vulpes vulpes        Present   

  abundance conservation_status  
0      Rare                 NaN  
1  Abundant                 NaN  
2    Common  Species of Concern  
3       NaN          Endangered  
4    Common                 NaN

In [6]:
# remove any rows with conservations status of extinct 
renamed_bio_df['conservation_status'].unique()

array([nan, 'Species of Concern', 'Endangered', 'In Recovery',
       'Threatened', 'Under Review', 'Proposed Threatened', 'Extinct',
       'Proposed Endangered', 'Resident', 'Breeder', 'Migratory'],
      dtype=object)

In [7]:
# Checking data count
renamed_bio_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 119248 entries, 0 to 119247
Data columns (total 6 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   species_id           119248 non-null  object
 1   park_name            119248 non-null  object
 2   scientific_name      119248 non-null  object
 3   occurrence           99106 non-null   object
 4   abundance            76306 non-null   object
 5   conservation_status  4718 non-null    object
dtypes: object(6)
memory usage: 5.5+ MB


In [8]:
# remove extinct from conservation status data (it is not relevant)
updated_bio_df = renamed_bio_df.loc[lambda renamed_bio_df: renamed_bio_df['conservation_status'] != 'Extinct']
print(updated_bio_df['conservation_status'].unique())
updated_bio_df.head()

[nan 'Species of Concern' 'Endangered' 'In Recovery' 'Threatened'
 'Under Review' 'Proposed Threatened' 'Proposed Endangered' 'Resident'
 'Breeder' 'Migratory']


species_id             park_name         scientific_name     occurrence  \
0  ACAD-1000  Acadia National Park             Alces alces        Present   
1  ACAD-1001  Acadia National Park  Odocoileus virginianus        Present   
2  ACAD-1002  Acadia National Park           Canis latrans        Present   
3  ACAD-1003  Acadia National Park             Canis lupus  Not Confirmed   
4  ACAD-1004  Acadia National Park           Vulpes vulpes        Present   

  abundance conservation_status  
0      Rare                 NaN  
1  Abundant                 NaN  
2    Common  Species of Concern  
3       NaN          Endangered  
4    Common                 NaN

In [9]:
# Checking data count
updated_bio_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 119247 entries, 0 to 119247
Data columns (total 6 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   species_id           119247 non-null  object
 1   park_name            119247 non-null  object
 2   scientific_name      119247 non-null  object
 3   occurrence           99105 non-null   object
 4   abundance            76306 non-null   object
 5   conservation_status  4717 non-null    object
dtypes: object(6)
memory usage: 6.4+ MB


In [10]:
# Remove any words after the work "Park" in park_names
p = '(.*Park)'
park_name_bio = updated_bio_df["park_name"].str.extract(p)

#Checking the regex function
park_name_bio.value_counts()

Great Smoky Mountains National Park           6623
Redwood National Park                         6310
Shenandoah National Park                      4655
Death Valley National Park                    4439
Yellowstone National Park                     3966
Crater Lake National Park                     3760
North Cascades National Park                  3363
Hawaii Volcanoes National Park                3298
Rocky Mountain National Park                  3152
Great Basin National Park                     2653
Grand Canyon National Park                    2622
Haleakala National Park                       2580
Glacier National Park                         2556
Mammoth Cave National Park                    2499
Congaree National Park                        2321
Joshua Tree National Park                     2294
Big Bend National Park                        2269
Yosemite National Park                        2088
Everglades National Park                      2084
Grand Teton National Park      

In [11]:
# exchange the new park_name column in the updated_bio_df
updated_bio_df["park_name"] = park_name_bio.values
updated_bio_df

C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


species_id             park_name         scientific_name  \
0       ACAD-1000  Acadia National Park             Alces alces   
1       ACAD-1001  Acadia National Park  Odocoileus virginianus   
2       ACAD-1002  Acadia National Park           Canis latrans   
3       ACAD-1003  Acadia National Park             Canis lupus   
4       ACAD-1004  Acadia National Park           Vulpes vulpes   
...           ...                   ...                     ...   
119243  ZION-2791    Zion National Park       Solanum triflorum   
119244  ZION-2792    Zion National Park         Vitis arizonica   
119245  ZION-2793    Zion National Park          Vitis vinifera   
119246  ZION-2794    Zion National Park       Larrea tridentata   
119247  ZION-2795    Zion National Park     Tribulus terrestris   

           occurrence abundance conservation_status  
0             Present      Rare                 NaN  
1             Present  Abundant                 NaN  
2             Present    Common  Species of Concern  
3       Not Confirmed       NaN          Endangered  
4             Present    Common                 NaN  
...               ...       ...                 ...  
119243        Present  Uncommon                 NaN  
119244        Present  Uncommon                 NaN  
119245        Present  Uncommon                 NaN  
119246        Present      Rare                 NaN  
119247        Present  Uncommon                 NaN  

[119247 rows x 6 columns]

In [12]:
# Create a variable that will store the counts of each species per park:
bio_count = updated_bio_df.groupby(["park_name"]).count()["species_id"]
print(bio_count)

park_name
Acadia National Park                          1709
Arches National Park                          1048
Badlands National Park                        1389
Big Bend National Park                        2269
Biscayne National Park                        1726
Black Canyon of the Gunnison National Park    1106
Bryce Canyon National Park                    1286
Canyonlands National Park                     1223
Capitol Reef National Park                    1566
Carlsbad Caverns National Park                1536
Channel Islands National Park                 1885
Congaree National Park                        2321
Crater Lake National Park                     3760
Cuyahoga Valley National Park                 1940
Death Valley National Park                    4439
Denali National Park                          1320
Dry Tortugas National Park                     848
Everglades National Park                      2084
Gates Of The Arctic National Park             1353
Glacier Bay National 

#### NOTE: Biodiversity data has been cleaned and put into updated_bio_df, 
#### NOTE: A variable is created to hold count of species per park (bio_count)

### Biodiversity Count Merge

#### Add in trails data below for merge:

In [13]:
# Load the trail data from trail_data.csv:

trails_data_to_load = "./Resources/trails_final.csv"
trails_final_df = pd.read_csv(trails_data_to_load, low_memory=False, encoding="utf-8")
trails_final_df.head(5)

trail_id                        name                   park_name  \
0  10020048     Harding Ice Field Trail  Kenai Fjords National Park   
1  10236086  Mount Healy Overlook Trail        Denali National Park   
2  10267857          Exit Glacier Trail  Kenai Fjords National Park   
3  10236076        Horseshoe Lake Trail        Denali National Park   
4  10236082          Triple Lakes Trail        Denali National Park   

              city_name state_name   country_name  \
0                Seward     Alaska  United States   
1  Denali National Park     Alaska  United States   
2                Seward     Alaska  United States   
3  Denali National Park     Alaska  United States   
4  Denali National Park     Alaska  United States   

                                _geoloc  popularity     length  \
0  {'lat': 60.18852, 'lng': -149.63156}     24.8931  15610.598   
1  {'lat': 63.73049, 'lng': -148.91968}     18.0311   6920.162   
2    {'lat': 60.18879, 'lng': -149.631}     17.7821   2896.812   
3    {'lat': 63.73661, 'lng': -148.915}     16.2674   3379.614   
4  {'lat': 63.73319, 'lng': -148.89682}     12.5935  29772.790   

   elevation_gain  difficulty_rating    route_type  visitor_usage  avg_rating  \
0       1161.8976                  5  out and back            3.0         5.0   
1        507.7968                  3  out and back            1.0         4.5   
2         81.9912                  1  out and back            3.0         4.5   
3        119.7864                  1          loop            2.0         4.5   
4       1124.7120                  5  out and back            1.0         4.5   

   num_reviews                                           features  \
0          423  ['dogs-no', 'forest', 'river', 'views', 'water...   
1          260  ['dogs-no', 'forest', 'views', 'wild-flowers',...   
2          224  ['dogs-no', 'partially-paved', 'views', 'wildl...   
3          237  ['dogs-no', 'forest', 'lake', 'kids', 'views',...   
4          110  ['dogs-no', 'lake', 'views', 'wild-flowers', '...   

                                          activities units  
0  ['birding', 'camping', 'hiking', 'nature-trips...     i  
1  ['birding', 'camping', 'hiking', 'nature-trips...     i  
2                              ['hiking', 'walking']     i  
3  ['birding', 'hiking', 'nature-trips', 'trail-r...     i  
4  ['birding', 'fishing', 'hiking', 'nature-trips...     i

In [14]:
# Create a value for the number of trails per park
# Sequoia and Kings Canyon National Park should equal 90 + 61):

trail_count = trails_final_df.groupby(["park_name"]).count()["trail_id"].sort_values(ascending=False)
trail_count

park_name
Great Smoky Mountains National Park           293
Yosemite National Park                        242
Yellowstone National Park                     228
Rocky Mountain National Park                  207
Shenandoah National Park                      187
Acadia National Park                          179
Olympic National Park                         170
Sequoia and Kings Canyon National Park        151
Glacier National Park                         132
Mount Rainier National Park                   130
Joshua Tree National Park                     108
Grand Teton National Park                     102
Grand Canyon National Park                     99
Zion National Park                             94
Death Valley National Park                     79
Canyonlands National Park                      77
Big Bend National Park                         70
Saguaro National Park                          60
Lassen Volcanic National Park                  59
Cuyahoga Valley National Park           

In [15]:
# Create a value for the average popularity score for all trails within a certain park:

trail_pop_avg = trails_final_df.groupby(["park_name"]).mean()["popularity"].sort_values(ascending=False)
print(trail_pop_avg)

park_name
Kenai Fjords National Park                    21.337600
Bryce Canyon National Park                    16.617903
Haleakala National Park                       13.723586
Arches National Park                          13.462423
Badlands National Park                        13.141040
Rocky Mountain National Park                  13.007846
Crater Lake National Park                     12.430750
Zion National Park                            12.027557
Mount Rainier National Park                   11.726444
Glacier National Park                         10.061925
Grand Canyon National Park                     9.716001
Pinnacles National Park                        9.421904
Olympic National Park                          9.389508
North Cascades National Park                   9.374660
Grand Teton National Park                      9.373725
Sequoia and Kings Canyon National Park         9.243440
Yosemite National Park                         9.235686
Capitol Reef National Park            

In [16]:
# Load the trail count pop data from trail_count_pop.csv:

trail_count_pop_to_load = "./Resources/trail_count_pop.csv"
trail_count_pop_df = pd.read_csv(trail_count_pop_to_load, low_memory=False, encoding="utf-8")
trail_count_pop_df.head(5)

park_name  trail_count  avg_popularity
0    Acadia National Park          179        8.375920
1    Arches National Park           48       13.462423
2  Badlands National Park           10       13.141040
3  Big Bend National Park           70        7.176380
4  Biscayne National Park            4        4.055200

#### Merge of trail_count, trail_pop_avg, bio_count DataFrames

In [17]:
# Create a new df that contains the count of trails, the average popularity of each park, and species count per park:

park_bio_df = pd.DataFrame({
    "trail_count": trail_count,
    "avg_popularity": trail_pop_avg,
    "species_count" : bio_count,
})

#Reset the index so the park name is no longer the index:

park_bio_df.reset_index(inplace=True)
park_bio_df = park_bio_df.rename(columns = {'index':'park_name'})

park_bio_df

park_name  trail_count  avg_popularity  \
0                Acadia National Park        179.0        8.375920   
1                Arches National Park         48.0       13.462423   
2              Badlands National Park         10.0       13.141040   
3              Big Bend National Park         70.0        7.176380   
4              Biscayne National Park          4.0        4.055200   
..                                ...          ...             ...   
57            Wolf Trap National Park          1.0        7.111900   
58  Wrangell - St Elias National Park          NaN             NaN   
59          Yellowstone National Park        228.0        7.006884   
60             Yosemite National Park        242.0        9.235686   
61                 Zion National Park         94.0       12.027557   

    species_count  
0          1709.0  
1          1048.0  
2          1389.0  
3          2269.0  
4          1726.0  
..            ...  
57            NaN  
58         1796.0  
59         3966.0  
60         2088.0  
61         1796.0  

[62 rows x 4 columns]

### Merge parks df with park bio data

In [18]:
# Load the park final data from parks_final.csv:

parks_final_data_to_load = "./Resources/parks_final.csv"
parks_final_df = pd.read_csv(parks_final_data_to_load, low_memory=False, encoding="utf-8")
parks_final_df.head(5)

park_code               park_name state   acres  latitude  longitude
0      ACAD    Acadia National Park    ME   47390     44.35     -68.21
1      ARCH    Arches National Park    UT   76519     38.68    -109.57
2      BADL  Badlands National Park    SD  242756     43.75    -102.50
3      BIBE  Big Bend National Park    TX  801163     29.25    -103.25
4      BISC  Biscayne National Park    FL  172924     25.65     -80.08

In [19]:
#Create a dataframe that populates the parks_df with trail count and popularity data from the trails df:
merged_parks_bio_df = pd.merge(parks_final_df, park_bio_df, on="park_name", how="left")
pd.options.display.max_rows = 100
merged_parks_bio_df

park_code                                   park_name       state    acres  \
0       ACAD                        Acadia National Park          ME    47390   
1       ARCH                        Arches National Park          UT    76519   
2       BADL                      Badlands National Park          SD   242756   
3       BIBE                      Big Bend National Park          TX   801163   
4       BISC                      Biscayne National Park          FL   172924   
5       BLCA  Black Canyon of the Gunnison National Park          CO    32950   
6       BRCA                  Bryce Canyon National Park          UT    35835   
7       CANY                   Canyonlands National Park          UT   337598   
8       CARE                  Capitol Reef National Park          UT   241904   
9       CAVE              Carlsbad Caverns National Park          NM    46766   
10      CHIS               Channel Islands National Park          CA   249561   
11      CONG                      Congaree National Park          SC    26546   
12      CRLA                   Crater Lake National Park          OR   183224   
13      CUVA               Cuyahoga Valley National Park          OH    32950   
14      DENA                        Denali National Park          AK  3372402   
15      DEVA                  Death Valley National Park      CA, NV  4740912   
16      DRTO                  Dry Tortugas National Park          FL    64701   
17      EVER                    Everglades National Park          FL  1508538   
18      GAAR           Gates Of The Arctic National Park          AK  7523898   
19      GLAC                       Glacier National Park          MT  1013572   
20      GLBA                   Glacier Bay National Park          AK  3224840   
21      GRBA                   Great Basin National Park          NV    77180   
22      GRCA                  Grand Canyon National Park          AZ  1217403   
23      GRSA              Great Sand Dunes National Park          CO    42984   
24      GRSM         Great Smoky Mountains National Park      TN, NC   521490   
25      GRTE                   Grand Teton National Park          WY   309995   
26      GUMO           Guadalupe Mountains National Park          TX    86416   
27      HALE                     Haleakala National Park          HI    29094   
28      HAVO              Hawaii Volcanoes National Park          HI   323431   
29      HOSP                   Hot Springs National Park          AR     5550   
30      ISRO                   Isle Royale National Park          MI   571790   
31      JOTR                   Joshua Tree National Park          CA   789745   
32      KATM                        Katmai National Park          AK  3674530   
33      KEFJ                  Kenai Fjords National Park          AK   669983   
34      KOVA                  Kobuk Valley National Park          AK  1750717   
35      LACL                    Lake Clark National Park          AK  2619733   
36      LAVO               Lassen Volcanic National Park          CA   106372   
37      MACA                  Mammoth Cave National Park          KY    52830   
38      MEVE                    Mesa Verde National Park          CO    52122   
39      MORA                 Mount Rainier National Park          WA   235625   
40      NOCA                North Cascades National Park          WA   504781   
41      OLYM                       Olympic National Park          WA   922651   
42      PEFO              Petrified Forest National Park          AZ    93533   
43      PINN                     Pinnacles National Park          CA    26606   
44      REDW                       Redwood National Park          CA   112512   
45      ROMO                Rocky Mountain National Park          CO   265828   
46      SAGU                       Saguaro National Park          AZ    91440   
47      SEKI      Sequoia and Kings Canyon National Park          CA   865952   
48      SHEN                    Sh

In [20]:
# Formatting the DataFrame
merged_parks_bio_df = merged_parks_bio_df.dropna(axis=0)
merged_parks_bio_df["trail_count"] = merged_parks_bio_df["trail_count"].map("{:,.0f}".format)
merged_parks_bio_df["avg_popularity"] = merged_parks_bio_df["avg_popularity"].map("{:.3f}".format)
merged_parks_bio_df["species_count"] = merged_parks_bio_df["species_count"].map("{:.0f}".format)
merged_parks_bio_df

C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy

park_code                                   park_name       state    acres  \
0       ACAD                        Acadia National Park          ME    47390   
1       ARCH                        Arches National Park          UT    76519   
2       BADL                      Badlands National Park          SD   242756   
3       BIBE                      Big Bend National Park          TX   801163   
4       BISC                      Biscayne National Park          FL   172924   
5       BLCA  Black Canyon of the Gunnison National Park          CO    32950   
6       BRCA                  Bryce Canyon National Park          UT    35835   
7       CANY                   Canyonlands National Park          UT   337598   
8       CARE                  Capitol Reef National Park          UT   241904   
9       CAVE              Carlsbad Caverns National Park          NM    46766   
10      CHIS               Channel Islands National Park          CA   249561   
11      CONG                      Congaree National Park          SC    26546   
12      CRLA                   Crater Lake National Park          OR   183224   
13      CUVA               Cuyahoga Valley National Park          OH    32950   
14      DENA                        Denali National Park          AK  3372402   
15      DEVA                  Death Valley National Park      CA, NV  4740912   
16      DRTO                  Dry Tortugas National Park          FL    64701   
17      EVER                    Everglades National Park          FL  1508538   
19      GLAC                       Glacier National Park          MT  1013572   
20      GLBA                   Glacier Bay National Park          AK  3224840   
21      GRBA                   Great Basin National Park          NV    77180   
22      GRCA                  Grand Canyon National Park          AZ  1217403   
23      GRSA              Great Sand Dunes National Park          CO    42984   
24      GRSM         Great Smoky Mountains National Park      TN, NC   521490   
25      GRTE                   Grand Teton National Park          WY   309995   
26      GUMO           Guadalupe Mountains National Park          TX    86416   
27      HALE                     Haleakala National Park          HI    29094   
28      HAVO              Hawaii Volcanoes National Park          HI   323431   
29      HOSP                   Hot Springs National Park          AR     5550   
30      ISRO                   Isle Royale National Park          MI   571790   
31      JOTR                   Joshua Tree National Park          CA   789745   
32      KATM                        Katmai National Park          AK  3674530   
33      KEFJ                  Kenai Fjords National Park          AK   669983   
36      LAVO               Lassen Volcanic National Park          CA   106372   
37      MACA                  Mammoth Cave National Park          KY    52830   
38      MEVE                    Mesa Verde National Park          CO    52122   
39      MORA                 Mount Rainier National Park          WA   235625   
40      NOCA                North Cascades National Park          WA   504781   
41      OLYM                       Olympic National Park          WA   922651   
42      PEFO              Petrified Forest National Park          AZ    93533   
43      PINN                     Pinnacles National Park          CA    26606   
44      REDW                       Redwood National Park          CA   112512   
45      ROMO                Rocky Mountain National Park          CO   265828   
46      SAGU                       Saguaro National Park          AZ    91440   
47      SEKI      Sequoia and Kings Canyon National Park          CA   865952   
48      SHEN                    Shenandoah National Park          VA   199045   
49      THRO            Theodore Roosevelt National Park          ND    70447   
50      VOYA                     Voyageurs National Park          MN   218200   
51      WICA                     W

In [21]:
# Write parks pop bio df to csv
merged_parks_bio_data_to_load = "./Resources/parks_pop_bio.csv"
merged_parks_bio_df.to_csv(merged_parks_bio_data_to_load, index=False)

### Biodiversity - Working Data Attempt 2

In [22]:
# Show DataFrame
bio_df.head()

Species ID             Park Name Category         Order    Family  \
0  ACAD-1000  Acadia National Park   Mammal  Artiodactyla  Cervidae   
1  ACAD-1001  Acadia National Park   Mammal  Artiodactyla  Cervidae   
2  ACAD-1002  Acadia National Park   Mammal     Carnivora   Canidae   
3  ACAD-1003  Acadia National Park   Mammal     Carnivora   Canidae   
4  ACAD-1004  Acadia National Park   Mammal     Carnivora   Canidae   

          Scientific Name                                       Common Names  \
0             Alces alces                                              Moose   
1  Odocoileus virginianus  Northern White-Tailed Deer, Virginia Deer, Whi...   
2           Canis latrans                             Coyote, Eastern Coyote   
3             Canis lupus        Eastern Timber Wolf, Gray Wolf, Timber Wolf   
4           Vulpes vulpes  Black Fox, Cross Fox, Eastern Red Fox, Fox, Re...   

  Record Status     Occurrence  Nativeness Abundance Seasonality  \
0      Approved        Present      Native      Rare    Resident   
1      Approved        Present      Native  Abundant         NaN   
2      Approved        Present  Not Native    Common         NaN   
3      Approved  Not Confirmed      Native       NaN         NaN   
4      Approved        Present     Unknown    Common     Breeder   

  Conservation Status Unnamed: 13  
0                 NaN         NaN  
1                 NaN         NaN  
2  Species of Concern         NaN  
3          Endangered         NaN  
4                 NaN         NaN

In [23]:
# Show Data in DataFrame
bio_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 119248 entries, 0 to 119247
Data columns (total 14 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   Species ID           119248 non-null  object
 1   Park Name            119248 non-null  object
 2   Category             119248 non-null  object
 3   Order                117776 non-null  object
 4   Family               117736 non-null  object
 5   Scientific Name      119248 non-null  object
 6   Common Names         119248 non-null  object
 7   Record Status        119248 non-null  object
 8   Occurrence           99106 non-null   object
 9   Nativeness           94203 non-null   object
 10  Abundance            76306 non-null   object
 11  Seasonality          20157 non-null   object
 12  Conservation Status  4718 non-null    object
 13  Unnamed: 13          5 non-null       object
dtypes: object(14)
memory usage: 12.7+ MB


In [24]:
# Show an array of Occurrence values
bio_df["Occurrence"].unique()

array(['Present', 'Not Confirmed', 'Not Present (Historical Report)',
       'Not Present (False Report)', 'Approved', nan, 'Not Present',
       'In Review'], dtype=object)

In [25]:
# Rework DataFrame with needed inforamation (and remove not needed information)
reduced_bio_df = bio_df[["Species ID", "Park Name", "Category", "Scientific Name",
                       "Occurrence", "Abundance", "Conservation Status"]].copy()
reduced_bio_df.head()

Species ID             Park Name Category         Scientific Name  \
0  ACAD-1000  Acadia National Park   Mammal             Alces alces   
1  ACAD-1001  Acadia National Park   Mammal  Odocoileus virginianus   
2  ACAD-1002  Acadia National Park   Mammal           Canis latrans   
3  ACAD-1003  Acadia National Park   Mammal             Canis lupus   
4  ACAD-1004  Acadia National Park   Mammal           Vulpes vulpes   

      Occurrence Abundance Conservation Status  
0        Present      Rare                 NaN  
1        Present  Abundant                 NaN  
2        Present    Common  Species of Concern  
3  Not Confirmed       NaN          Endangered  
4        Present    Common                 NaN

In [26]:
# Standardize column names
renamed_bio_df = reduced_bio_df.rename(columns={"Species ID": "species_id",
                                        "Park Name": "park_name",
                                        "Category": "category",       
                                        "Scientific Name": "scientific_name",
                                        "Occurrence": "occurrence",
                                        "Abundance": "abundance",
                                        "Conservation Status": "conservation_status",
                                       })
renamed_bio_df.head()

species_id             park_name category         scientific_name  \
0  ACAD-1000  Acadia National Park   Mammal             Alces alces   
1  ACAD-1001  Acadia National Park   Mammal  Odocoileus virginianus   
2  ACAD-1002  Acadia National Park   Mammal           Canis latrans   
3  ACAD-1003  Acadia National Park   Mammal             Canis lupus   
4  ACAD-1004  Acadia National Park   Mammal           Vulpes vulpes   

      occurrence abundance conservation_status  
0        Present      Rare                 NaN  
1        Present  Abundant                 NaN  
2        Present    Common  Species of Concern  
3  Not Confirmed       NaN          Endangered  
4        Present    Common                 NaN

In [27]:
# Replace NaN values with "None"
renamed_bio_df = renamed_bio_df.replace(np.nan, 'None')
renamed_bio_df

species_id             park_name        category  \
0       ACAD-1000  Acadia National Park          Mammal   
1       ACAD-1001  Acadia National Park          Mammal   
2       ACAD-1002  Acadia National Park          Mammal   
3       ACAD-1003  Acadia National Park          Mammal   
4       ACAD-1004  Acadia National Park          Mammal   
...           ...                   ...             ...   
119243  ZION-2791    Zion National Park  Vascular Plant   
119244  ZION-2792    Zion National Park  Vascular Plant   
119245  ZION-2793    Zion National Park  Vascular Plant   
119246  ZION-2794    Zion National Park  Vascular Plant   
119247  ZION-2795    Zion National Park  Vascular Plant   

               scientific_name     occurrence abundance conservation_status  
0                  Alces alces        Present      Rare                None  
1       Odocoileus virginianus        Present  Abundant                None  
2                Canis latrans        Present    Common  Species of Concern  
3                  Canis lupus  Not Confirmed      None          Endangered  
4                Vulpes vulpes        Present    Common                None  
...                        ...            ...       ...                 ...  
119243       Solanum triflorum        Present  Uncommon                None  
119244         Vitis arizonica        Present  Uncommon                None  
119245          Vitis vinifera        Present  Uncommon                None  
119246       Larrea tridentata        Present      Rare                None  
119247     Tribulus terrestris        Present  Uncommon                None  

[119248 rows x 7 columns]

In [28]:
# remove "not present" in occurrence column
working_bio_df = renamed_bio_df.loc[renamed_bio_df['occurrence'].isin(['Present', 'Not Confirmed', 'Approved', 'None', 'In Review'])]
print(working_bio_df['occurrence'].unique())
working_bio_df

['Present' 'Not Confirmed' 'Approved' 'None' 'In Review']


species_id             park_name        category  \
0       ACAD-1000  Acadia National Park          Mammal   
1       ACAD-1001  Acadia National Park          Mammal   
2       ACAD-1002  Acadia National Park          Mammal   
3       ACAD-1003  Acadia National Park          Mammal   
4       ACAD-1004  Acadia National Park          Mammal   
...           ...                   ...             ...   
119243  ZION-2791    Zion National Park  Vascular Plant   
119244  ZION-2792    Zion National Park  Vascular Plant   
119245  ZION-2793    Zion National Park  Vascular Plant   
119246  ZION-2794    Zion National Park  Vascular Plant   
119247  ZION-2795    Zion National Park  Vascular Plant   

               scientific_name     occurrence abundance conservation_status  
0                  Alces alces        Present      Rare                None  
1       Odocoileus virginianus        Present  Abundant                None  
2                Canis latrans        Present    Common  Species of Concern  
3                  Canis lupus  Not Confirmed      None          Endangered  
4                Vulpes vulpes        Present    Common                None  
...                        ...            ...       ...                 ...  
119243       Solanum triflorum        Present  Uncommon                None  
119244         Vitis arizonica        Present  Uncommon                None  
119245          Vitis vinifera        Present  Uncommon                None  
119246       Larrea tridentata        Present      Rare                None  
119247     Tribulus terrestris        Present  Uncommon                None  

[115435 rows x 7 columns]

In [29]:
# Show Values
working_bio_df["occurrence"].value_counts()

Present          83278
None             20142
Not Confirmed    11958
Approved            51
In Review            6
Name: occurrence, dtype: int64

In [30]:
# Show an array of Abundance values
working_bio_df["abundance"].unique()

array(['Rare', 'Abundant', 'Common', 'None', 'Uncommon', 'Occasional',
       'Unknown', 'Not Native', 'Native'], dtype=object)

In [31]:
# Categorize Abundance based on rare and not rare (Rare/Uncommon = FALSE, Rest = TRUE)
# This will encode into 1's and 0's for machine learning in future
# You can use this pseudocode for future column cleaning
working_bio_df['abundance'] = working_bio_df['abundance'].replace(['Rare','Uncommon'],'FALSE')
working_bio_df

C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


species_id             park_name        category  \
0       ACAD-1000  Acadia National Park          Mammal   
1       ACAD-1001  Acadia National Park          Mammal   
2       ACAD-1002  Acadia National Park          Mammal   
3       ACAD-1003  Acadia National Park          Mammal   
4       ACAD-1004  Acadia National Park          Mammal   
...           ...                   ...             ...   
119243  ZION-2791    Zion National Park  Vascular Plant   
119244  ZION-2792    Zion National Park  Vascular Plant   
119245  ZION-2793    Zion National Park  Vascular Plant   
119246  ZION-2794    Zion National Park  Vascular Plant   
119247  ZION-2795    Zion National Park  Vascular Plant   

               scientific_name     occurrence abundance conservation_status  
0                  Alces alces        Present     FALSE                None  
1       Odocoileus virginianus        Present  Abundant                None  
2                Canis latrans        Present    Common  Species of Concern  
3                  Canis lupus  Not Confirmed      None          Endangered  
4                Vulpes vulpes        Present    Common                None  
...                        ...            ...       ...                 ...  
119243       Solanum triflorum        Present     FALSE                None  
119244         Vitis arizonica        Present     FALSE                None  
119245          Vitis vinifera        Present     FALSE                None  
119246       Larrea tridentata        Present     FALSE                None  
119247     Tribulus terrestris        Present     FALSE                None  

[115435 rows x 7 columns]

In [32]:
# Categorize Abundance based on rare and not rare (Rare/Uncommon = FALSE, Rest = TRUE)
# This will encode into 1's and 0's for machine learning in future
# You can use this pseudocode for future column cleaning

working_bio_df['abundance'] = working_bio_df['abundance'].replace(['Abundant', 'Common', 'None', 'Occasional',
       'Unknown', 'Not Native', 'Native'],'TRUE')
working_bio_df

C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


species_id             park_name        category  \
0       ACAD-1000  Acadia National Park          Mammal   
1       ACAD-1001  Acadia National Park          Mammal   
2       ACAD-1002  Acadia National Park          Mammal   
3       ACAD-1003  Acadia National Park          Mammal   
4       ACAD-1004  Acadia National Park          Mammal   
...           ...                   ...             ...   
119243  ZION-2791    Zion National Park  Vascular Plant   
119244  ZION-2792    Zion National Park  Vascular Plant   
119245  ZION-2793    Zion National Park  Vascular Plant   
119246  ZION-2794    Zion National Park  Vascular Plant   
119247  ZION-2795    Zion National Park  Vascular Plant   

               scientific_name     occurrence abundance conservation_status  
0                  Alces alces        Present     FALSE                None  
1       Odocoileus virginianus        Present      TRUE                None  
2                Canis latrans        Present      TRUE  Species of Concern  
3                  Canis lupus  Not Confirmed      TRUE          Endangered  
4                Vulpes vulpes        Present      TRUE                None  
...                        ...            ...       ...                 ...  
119243       Solanum triflorum        Present     FALSE                None  
119244         Vitis arizonica        Present     FALSE                None  
119245          Vitis vinifera        Present     FALSE                None  
119246       Larrea tridentata        Present     FALSE                None  
119247     Tribulus terrestris        Present     FALSE                None  

[115435 rows x 7 columns]

In [33]:
# Show data values
working_bio_df["conservation_status"].value_counts()

None                   111023
Species of Concern       3665
Endangered                295
Under Review              175
Threatened                165
In Recovery                74
Proposed Endangered        18
Breeder                     7
Proposed Threatened         6
Resident                    5
Migratory                   2
Name: conservation_status, dtype: int64

In [34]:
# Show an array of Conservation Status values
working_bio_df["conservation_status"].unique()

array(['None', 'Species of Concern', 'Endangered', 'In Recovery',
       'Threatened', 'Under Review', 'Proposed Threatened',
       'Proposed Endangered', 'Resident', 'Breeder', 'Migratory'],
      dtype=object)

In [35]:
# Categorize Conservation based on having a status vs. None
# This will encode into 1's and 0's for machine learning in future
# You can use this pseudocode for future column cleaning
working_bio_df['conservation_status'] = working_bio_df['conservation_status'].replace(['Species of Concern', 'Endangered', 'In Recovery',
       'Threatened', 'Under Review', 'Proposed Threatened','Proposed Endangered', 'Resident', 'Breeder', 'Migratory'],'TRUE')

working_bio_df['conservation_status'] = working_bio_df['conservation_status'].replace(['None'],'FALSE')
working_bio_df

C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
C:\Users\16are\anaconda3\envs\mlenv2\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


species_id             park_name        category  \
0       ACAD-1000  Acadia National Park          Mammal   
1       ACAD-1001  Acadia National Park          Mammal   
2       ACAD-1002  Acadia National Park          Mammal   
3       ACAD-1003  Acadia National Park          Mammal   
4       ACAD-1004  Acadia National Park          Mammal   
...           ...                   ...             ...   
119243  ZION-2791    Zion National Park  Vascular Plant   
119244  ZION-2792    Zion National Park  Vascular Plant   
119245  ZION-2793    Zion National Park  Vascular Plant   
119246  ZION-2794    Zion National Park  Vascular Plant   
119247  ZION-2795    Zion National Park  Vascular Plant   

               scientific_name     occurrence abundance conservation_status  
0                  Alces alces        Present     FALSE               FALSE  
1       Odocoileus virginianus        Present      TRUE               FALSE  
2                Canis latrans        Present      TRUE                TRUE  
3                  Canis lupus  Not Confirmed      TRUE                TRUE  
4                Vulpes vulpes        Present      TRUE               FALSE  
...                        ...            ...       ...                 ...  
119243       Solanum triflorum        Present     FALSE               FALSE  
119244         Vitis arizonica        Present     FALSE               FALSE  
119245          Vitis vinifera        Present     FALSE               FALSE  
119246       Larrea tridentata        Present     FALSE               FALSE  
119247     Tribulus terrestris        Present     FALSE               FALSE  

[115435 rows x 7 columns]

In [36]:
# Write working_bio_df to CSV:

merged_data_to_load = "./Resources/working_bio_df.csv"
working_bio_df.to_csv(merged_data_to_load, index=False)

## Grouping Bio and Trails Data for Machine Learning

### Add aggregated fields from the working_bio_df to trails_final_df

In [37]:
print(working_bio_df.info())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 115435 entries, 0 to 119247
Data columns (total 7 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   species_id           115435 non-null  object
 1   park_name            115435 non-null  object
 2   category             115435 non-null  object
 3   scientific_name      115435 non-null  object
 4   occurrence           115435 non-null  object
 5   abundance            115435 non-null  object
 6   conservation_status  115435 non-null  object
dtypes: object(7)
memory usage: 7.0+ MB
None


In [38]:
# Show an array of various column values
print(working_bio_df["species_id"].unique()) # not needed in final df
print(working_bio_df["park_name"].unique()) # group by park
print(working_bio_df["category"].unique()) # count category
print(working_bio_df["scientific_name"].unique()) # count names
print(working_bio_df["occurrence"].unique()) # will be deleted
print(working_bio_df["abundance"].unique()) # column has been cleaned for ML
print(working_bio_df["conservation_status"].unique()) # column has been cleaned for ML

['ACAD-1000' 'ACAD-1001' 'ACAD-1002' ... 'ZION-2793' 'ZION-2794'
 'ZION-2795']
['Acadia National Park' 'Arches National Park' 'Badlands National Park'
 'Big Bend National Park' 'Biscayne National Park'
 'Black Canyon of the Gunnison National Park' 'Bryce Canyon National Park'
 'Canyonlands National Park' 'Capitol Reef National Park'
 'Carlsbad Caverns National Park' 'Channel Islands National Park'
 'Congaree National Park' 'Crater Lake National Park'
 'Cuyahoga Valley National Park' 'Denali National Park and Preserve'
 'Death Valley National Park' 'Dry Tortugas National Park'
 'Everglades National Park'
 'Gates Of The Arctic National Park and Preserve' 'Glacier National Park'
 'Glacier Bay National Park and Preserve' 'Great Basin National Park'
 'Grand Canyon National Park'
 'Great Sand Dunes National Park and Preserve'
 'Great Smoky Mountains National Park' 'Grand Teton National Park'
 'Guadalupe Mountains National Park' 'Haleakala National Park'
 'Hawaii Volcanoes National Park' 'Hot

In [39]:
# import csv from sql as dataframes

file_path1 = "./Resources/bio_category.csv"
bio_category_df = pd.read_csv(file_path1, low_memory=False)
bio_category_df.head()


park_name   category  count
0  Acadia National Park       Bird    331
1  Acadia National Park  Amphibian     12
2  Acadia National Park     Mammal     48
3  Acadia National Park       Fish     34
4  Acadia National Park    Reptile     10

In [40]:
# import csv from sql as dataframes

file_path2 = "./Resources/bio_count_per_park.csv"
bio_count_per_park_df = pd.read_csv(file_path2, low_memory=False)
bio_count_per_park_df.head()

park_name  count
0    Acadia National Park   1572
1    Arches National Park   1006
2  Badlands National Park   1365
3  Big Bend National Park   2258
4  Biscayne National Park   1590

In [41]:
# create new dataframe for count of bio categories
# count_bio_categories_df = pd.DataFrame(columns=('park_name',
#                                                 'Algae',
#                                                 'Amphibian',
#                                                 'Bird',
#                                                 'Crab/Lobster/Shrimp',
#                                                 'Fish',
#                                                 'Fungi',
#                                                 'Insect',
#                                                 'Invertebrate',
#                                                 'Mammal',
#                                                 'Nonvascular Plant',
#                                                 'Reptile',
#                                                 'Slug/Snail',
#                                                 'Spider/Scorpion',
#                                                 'Vascular Plant'))                 

# #count_bio_categories_df

# count_bio_categories_df.append(bio_category_df)

# count_bio_categories_df.head() DIDNT WORK ############

# create new dataframe for count of bio categories

count_bio_categories_df = bio_category_df.groupby(['park_name','category']).sum(['category'])
count_bio_categories_df

count
park_name            category             
Acadia National Park Amphibian          12
                     Bird              331
                     Fish               34
                     Mammal             48
                     Reptile            10
...                                    ...
Zion National Park   Bird              297
                     Fish               15
                     Mammal             80
                     Reptile            30
                     Vascular Plant   1237

[547 rows x 1 columns]

In [42]:
# Write count_bio_categories_df to CSV:

merged_data_to_load = "./Resources/count_bio_categories.csv"
count_bio_categories_df.to_csv(merged_data_to_load, index=False)

In [43]:
# create a count of total different species categories per park
count_bio_categories = bio_category_df.groupby(['park_name']).count()['category']
count_bio_categories

park_name
Acadia National Park                               6
Arches National Park                               6
Badlands National Park                            10
Big Bend National Park                             7
Biscayne National Park                             8
Black Canyon of the Gunnison National Park         6
Bryce Canyon National Park                         6
Canyonlands National Park                          6
Capitol Reef National Park                         6
Carlsbad Caverns National Park                     6
Channel Islands National Park                     13
Congaree National Park                            14
Crater Lake National Park                         14
Cuyahoga Valley National Park                     11
Death Valley National Park                        14
Denali National Park and Preserve                  9
Dry Tortugas National Park                         6
Everglades National Park                           6
Gates Of The Arctic National Park an

In [44]:
# count of bio categories
cat_count = working_bio_df.groupby(["park_name"]).count()["category"]
cat_count

park_name
Acadia National Park                              1572
Arches National Park                              1006
Badlands National Park                            1365
Big Bend National Park                            2258
Biscayne National Park                            1590
Black Canyon of the Gunnison National Park        1099
Bryce Canyon National Park                        1189
Canyonlands National Park                         1166
Capitol Reef National Park                        1456
Carlsbad Caverns National Park                    1528
Channel Islands National Park                     1874
Congaree National Park                            2311
Crater Lake National Park                         3741
Cuyahoga Valley National Park                     1906
Death Valley National Park                        4386
Denali National Park and Preserve                 1309
Dry Tortugas National Park                         779
Everglades National Park                          1903


In [45]:
# create df of parks and species_count, category_count, and scientific_name count
biocount_parks_df = pd.DataFrame({
    "species_count" : cat_count,
    "bio_category_count":count_bio_categories
})

#Reset the index so the park name is no longer the index:

biocount_parks_df.reset_index(inplace=True)
biocount_parks_df = biocount_parks_df.rename(columns = {'index':'park_name'})

biocount_parks_df


park_name  species_count  \
0                             Acadia National Park           1572   
1                             Arches National Park           1006   
2                           Badlands National Park           1365   
3                           Big Bend National Park           2258   
4                           Biscayne National Park           1590   
5       Black Canyon of the Gunnison National Park           1099   
6                       Bryce Canyon National Park           1189   
7                        Canyonlands National Park           1166   
8                       Capitol Reef National Park           1456   
9                   Carlsbad Caverns National Park           1528   
10                   Channel Islands National Park           1874   
11                          Congaree National Park           2311   
12                       Crater Lake National Park           3741   
13                   Cuyahoga Valley National Park           1906   
14                      Death Valley National Park           4386   
15               Denali National Park and Preserve           1309   
16                      Dry Tortugas National Park            779   
17                        Everglades National Park           1903   
18  Gates Of The Arctic National Park and Preserve           1351   
19          Glacier Bay National Park and Preserve           1878   
20                           Glacier National Park           2475   
21                      Grand Canyon National Park           2604   
22                       Grand Teton National Park           2020   
23                       Great Basin National Park           2595   
24     Great Sand Dunes National Park and Preserve            947   
25             Great Smoky Mountains National Park           6100   
26               Guadalupe Mountains National Park           1730   
27                         Haleakala National Park           2425   
28                  Hawaii Volcanoes National Park           3038   
29                       Hot Springs National Park           1531   
30                       Isle Royale National Park           1333   
31                       Joshua Tree National Park           2259   
32               Katmai National Park and Preserve           1192   
33                      Kenai Fjords National Park           1015   
34                      Kobuk Valley National Park           1025   
35           Lake Clark National Park and Preserve           1990   
36                   Lassen Volcanic National Park           1702   
37                      Mammoth Cave National Park           2445   
38                        Mesa Verde National Park           1226   
39                     Mount Rainier National Park           1712   
40                    North Cascades National Park           3356   
41                           Olympic National Park           1917   
42                  Petrified Forest National Park            818   
43                         Pinnacles National Park           1379   
44                           Redwood National Park           6268   
45                    Rocky Mountain National Park           3135   
46                           Saguaro National Park           1806   
47         Sequoia and Kings Canyon National Parks           1978   
48                        Shenandoah National Park           4563   
49                Theodore Roosevelt National Park           1152   
50                         Voyageurs National Park           1448   
51                         Wind Cave National Park           1225   
52  Wrangell - St Elias National Park and Preserve           1750   
53                       Yellowstone National Park           3900   
54                          Yosemite National Park           2043   
55                              Zion National Park           1666   

    bio_category_count  
0                    6  
1                    6  
2                   10  
3      

In [46]:
merged_trails_bio_df = pd.merge(trails_final_df, biocount_parks_df, on="park_name", how="inner")
pd.options.display.max_rows = 150000
merged_trails_bio_df

trail_id                                               name  \
0     10020048                            Harding Ice Field Trail   
1     10267857                                 Exit Glacier Trail   
2     10187810  Bright Angel Trail to Bright Angel Campground ...   
3     10016964                  South Kaibab Trail to Cedar Ridge   
4     10237812        Three-Mile Resthouse via Bright Angel Trail   
5     10245012  South Kaibab, Phantom Ranch, and Bright Angel ...   
6     10265905                South Kaibab Trail to Ooh Aah Point   
7     10266148                             Grand Canyon Rim Trail   
8     10094721   Rim-to-Rim: North Kaibab to Grand Canyon Village   
9     10026816                               Shoshone Point Trail   
10    10235665         Plateau Point Trail via Bright Angel Trail   
11    10266521               South Kaibab Trail to Skeleton Point   
12    10016127                        Grand Canyon West Rim Trail   
13    10337353          1.5 Mile Resthouse via Bright Angel Trail   
14    10013850                           Bright Angel Point Trail   
15    10304374               Indian Garden via Bright Angel Trail   
16    10004120                               Grandview Trail Loop   
17    10006500                                       Hermit Trail   
18    10259347            Grandview Point to Horseshoe Mesa Trail   
19    10041313              North Kaibab Trail to Roaring Springs   
20    10286650                South Kaibab Trail to Phantom Ranch   
21    10031336                                     Widforss Trail   
22    10031337                                     Transept Trail   
23    10304469                        Yavapai Point via Rim Trail   
24    10273263     Bright Angel Trail: South Rim to Phantom Ranch   
25    10000811                                   Cape Royal Trail   
26    10009957  Rim-to-Rim: North Kaibab to South Kaibab Trail...   
27    10297089  Rim to Rim Trail Segment: Indian Garden to Col...   
28    10040243               North Kaibab Trail to Colorado River   
29    10026822                                         Cape Final   
30    10255289  Phantom Ranch to Ribbon Falls via North Kaibab...   
31    10258667  North Kaibab Trail to Supai Tunnel and Coconin...   
32    10258648     Hermit's Rest Viewpoint  to Santa Maria Spring   
33    10257085  South Kaibab to North Kaibab to Bright Angel T...   
34    10265749  Bright Angel Trail to Phantom Overlook to Sout...   
35    10315767                      South Kaibab Trail to Tip Off   
36    10023828  Grand Canyon South Rim Scenic Drive: Cameron t...   
37    10042232      Thunder Creek to Deer Creek and Thunder Falls   
38    10365390        Rim to Rim: North to South and Ribbon Falls   
39    10258317          Grand Canyon Rim Village to Hermit's Rest   
40    10002324                   Desert View Visitor Center Trail   
41    10274527                                  Coconino Overlook   
42    10009628                                    Uncle Jim Trail   
43    10009444  Dripping Springs via Dripping Springs and Herm...   
44    10331092               North Kaibab Trail to Redwall Bridge   
45    10259343                                       Tanner Trail   
46    10304719         South Kaibab, Tonto and Bright Angel Trail   
47    10246734                        South to North Kaibab Trail   
48    10258602                                     Point Imperial   
49    10302747       West Rim Trail: Hermits Rest to Powell Point   
50    10235597                              Roosevelt Point Trail   
51    10013382                                   South Bass Trail   
52    10258739                          The Escalante Route Trail   
53    10023951                                    Nankoweap Trail   
54    10272964                   Hermit Trail to Dripping Springs   
55    10258650                                Cliff Springs Trail   
56    10258659                                  Walhalla Overlook   
57  

In [47]:
# Write merged_trails_bio_df to CSV:

merged_data_to_load = "./Resources/trails_bio_combined.csv"
merged_trails_bio_df.to_csv(merged_data_to_load, index=False)